Part 1: Load required libraries.

In [1]:
import torchvision.models as models
from torchsummary import summary
import torch
device = torch.device("cuda")
import pretrainedmodels
from PIL import Image
import requests
import time
import pretrainedmodels.utils as utils
import numpy as np
import matplotlib.pyplot as plt
import cma
from es import SimpleGA, CMAES, PEPG, OpenES
from skimage.draw import line_aa
from skimage.draw import circle
import torchvision
from random import randint
print (device)

###############################

cuda


Part 2: Define other constants and helper functions

In [2]:
LABELS_URL = 'https://s3.amazonaws.com/mlpipes/pytorch-quick-start/labels.json'
IMG_URL = 'https://s3.amazonaws.com/mlpipes/pytorch-quick-start/cat.jpg'

labels = {int(key):value for (key, value)
          in requests.get(LABELS_URL).json().items()}

model_names = ['resnet18', 'squeezenet1_0', 'squeezenet1_1', 'resnet50', 'vgg11_bn', 'vgg19', 'vgg16', 'resnet34', 'vgg13', 
               'densenet201', 'vgg13_bn', 'resnet152', 'vgg16_bn', 'resnet101', 
               'vgg19_bn', 'vgg11', 'alexnet', 'inceptionv3']


def visualize_torch(img):
    plt.figure()
    plt.imshow(torchvision.utils.make_grid(img, nrow=5).permute(1, 2, 0))
    
def torch_softmax(predictions):
    m = torch.nn.Softmax(dim=0)
    return m(predictions)

def softmax(x):
    e_x = np.exp(x - np.max(x))
    return e_x / e_x.sum(axis=0)

def top_n_indices(arr, n):
    tmp = arr.argsort()[-1*n:][::-1]
    return list(tmp)

def prep_image_for_inference(img_path):
    input_img = load_img(img_path)
    input_tensor = tf_img(input_img)
    input_tensor = input_tensor.unsqueeze(0)
    input_to_model = torch.autograd.Variable(input_tensor,
            requires_grad=False)
#     input_to_model -= torch.min(input_to_model)
#     input_to_model = input_to_model / torch.max(input_to_model)
    return input_to_model

def get_probabilities(logits):
    logits_numpy = logits.detach().numpy()
    return softmax(logits_numpy[0])

def torch_image_to_numpy(img):
    input_img = img.detach().numpy()
    return input_img

def prep_torch_img_for_viewing(img):
    return torchvision.utils.make_grid(img, nrow=5).permute(1, 2, 0)

def prep_numpy_img_for_viewing(img):
    img = img[0,:,:,:]
    print (img.shape)
    img = np.reshape(img, [299, 299, 3])
    return img

def numpy_img_from_path(img_path):
    input_img = load_img(img_path)
    return np.asarray(input_img)

model_name = 'inceptionv3'
model = pretrainedmodels.__dict__[model_name](num_classes=1000, pretrained='imagenet')
model.eval()
model.to(device)

Inception3(
  (Conv2d_1a_3x3): BasicConv2d(
    (conv): Conv2d(3, 32, kernel_size=(3, 3), stride=(2, 2), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2a_3x3): BasicConv2d(
    (conv): Conv2d(32, 32, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(32, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_2b_3x3): BasicConv2d(
    (conv): Conv2d(32, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
    (bn): BatchNorm2d(64, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_3b_1x1): BasicConv2d(
    (conv): Conv2d(64, 80, kernel_size=(1, 1), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(80, eps=0.001, momentum=0.1, affine=True, track_running_stats=True)
  )
  (Conv2d_4a_3x3): BasicConv2d(
    (conv): Conv2d(80, 192, kernel_size=(3, 3), stride=(1, 1), bias=False)
    (bn): BatchNorm2d(192, eps=0.001, momentum=0.1, affine=True, t

Part 3: Load other target images and their labels

In [3]:
# Load in the filenames 
import os
path = '/home/malhar/Desktop/data/'

imagenet_validation_filenames_path = path + 'imagenet_validation_filenames.txt'
imagenet_validation_sys_labels_path = path + 'imagenet_2012_validation_synset_labels.txt'
imagenet_validation_word_labels_path = path + 'synset_labels_to_words.txt'

imagenet_validation_filenames = []
imagenet_validation_sys_labels = []
imagenet_validation_word_labels = []



with open(imagenet_validation_filenames_path) as f:
    for line in f:
        imagenet_validation_filenames.append(line.rstrip('\n'))
        
with open(imagenet_validation_sys_labels_path) as f:
    for line in f:
        imagenet_validation_sys_labels.append(line.rstrip('\n'))
                
with open(imagenet_validation_word_labels_path) as f:
    for line in f:
        imagenet_validation_word_labels.append(line.rstrip('\n'))
        
import random

RANGE = 50000
NUMBER_OF_FILES = 100
random_filename_numbers = random.sample(xrange(RANGE), NUMBER_OF_FILES)

# Get the randomly chosen files
random_filenames = [imagenet_validation_filenames[i] for i in random_filename_numbers]
corresponding_sysnet_labels = [imagenet_validation_sys_labels[i] for i in random_filename_numbers]
corresponding_index_labels = []

for sysnet_label in corresponding_sysnet_labels:
    index = [idx for idx, s in enumerate(imagenet_validation_word_labels) if sysnet_label in s][0]
    corresponding_index_labels.append(index)

Part 4: Define other stuff, like the custom fitness function 

In [4]:

# Define the fitness function
# from https://github.com/CMA-ES/pycma/blob/master/cma/fitness_functions.py
def custom_fitness_function(model, img, original_class, target_class, rr, cc, solution_vector, option):
    
    size = len(solution_vector)
    
    r_vector = torch.from_numpy(solution_vector[0:size/3])
    r_vector = r_vector.type(torch.float)
    r_vector = r_vector.to(device)
    
    g_vector = torch.from_numpy(solution_vector[size/3: int(2*size/3)])
    g_vector = g_vector.type(torch.float)
    g_vector = g_vector.to(device)
    
    b_vector = torch.from_numpy(solution_vector[int(2*size/3): size]).to(device)
    b_vector = b_vector.type(torch.float)
    b_vector = b_vector.to(device)
    
    img[0,0,rr,cc] = r_vector
    img[0,1,rr,cc] = g_vector
    img[0,2,rr,cc] = b_vector
    
#     img[img < -1] = -1
#     img[img > 1] = 1
    
    prediction = model(img)
    probabilities = torch_softmax(prediction[0])
    
#     print ('Target class: ', probabilities[target_class].detach().cpu().numpy(), 
#            ':: Original class: ', probabilities[original_class].detach().cpu().numpy())
#     print ('Top scorer: ', labels[int(torch.argmax(probabilities))])
    
    # Option 1 aka trash
    # NVM it actually isnt too bad; just less descendants per generation and more generations. Does't converge to 
    # what we want though
    if (option == 0):
        # Get the target class probability - we want to maximize this
        target_class_prob = torch.log(probabilities[target_class])
        
        # Get the probability vectors in numpy format
        numpy_probs = probabilities.detach().cpu().numpy()
        
        # Get the top k indices that have the max probabilities
        top_k = (top_n_indices(numpy_probs, 5))
        
        top_k_probs = probabilities[top_k]
        
        # If the target class is in the top k, we need to take some precautions. We need to set that value to 0
        if (int(target_class) in top_k):
            
            # Find the index where the target class is in the top k
            index = top_k.index(target_class)
#             top_k[index] = 0

            # Set that value to zero
            top_k_probs[index] = 0
            
        
#         print torch.sum(torch.log(top_k_probs))
#         original_class_prob = (torch.sum(torch.log(top_k_probs)))    
        original_class_prob = torch.log(probabilities[original_class])
        fitness = 10 * (target_class_prob)  - (original_class_prob)
#         print (target_class_prob, original_class_prob, fitness)

#         target_class_prob = torch.log(probabilities[target_class])
#         original_class_prob = torch.log(probabilities[original_class])
#         fitness = target_class_prob - original_class_prob
    
        
    # Maximize target class probability and minimize non-target class probability; squeeze all probability into target
    elif (option == 1):
        target_class_prob = torch.log(probabilities[target_class])
        
        top_scorer_index = int(torch.argmax(probabilities))
        
        top_scorer_loss = 0
        
        if (top_scorer_index != target_class):
            top_scorer_loss = torch.log(probabilities[top_scorer_index])
        
        everything_log = probabilities
        everything_log[target_class] = 1
        everything_log = torch.log(everything_log)
        non_target_class_fitness = torch.sum(everything_log)
        fitness = target_class_prob - non_target_class_fitness #- top_scorer_loss
    
    elif (option == 2):
        target_class_prob = torch.log(probabilities[target_class])
        everything_log = probabilities
        everything_log[target_class] = 1
        everything_log = torch.log(everything_log)
        non_target_class_fitness = torch.sum(everything_log)
        entropy = torch.dot(torch.log(probabilities), probabilities)
        fitness = target_class_prob - non_target_class_fitness - entropy
    
    return fitness

# fit_func = rastrigin
fit_func = custom_fitness_function

def get_predictions_from_temp_array(result, original_class, target_class, rr, cc):
    adversarial_scratch = result[0]
    
    size = len(adversarial_scratch)
    
    r_vector = torch.from_numpy(adversarial_scratch[0:size/3])
    r_vector = r_vector.type(torch.float)
    r_vector = r_vector.to(device)

    g_vector = torch.from_numpy(adversarial_scratch[size/3: int(2*size/3)])
    g_vector = g_vector.type(torch.float)
    g_vector = g_vector.to(device)

    b_vector = torch.from_numpy(adversarial_scratch[int(2*size/3): size]).to(device)
    b_vector = b_vector.type(torch.float)
    b_vector = b_vector.to(device)
    
    input_to_model_temp = prep_image_for_inference(path_img)
    input_to_model_temp = input_to_model_temp.to(device)
    input_to_model_temp[0,0,rr,cc] = r_vector
    input_to_model_temp[0,1,rr,cc] = g_vector
    input_to_model_temp[0,2,rr,cc] = b_vector
    
    initial_logits_tmp = model(input_to_model_temp)

    initial_probabilities_tmp = get_probabilities(initial_logits_tmp.cpu())
    
    return initial_probabilities_tmp[original_class], initial_probabilities_tmp[target_class], initial_probabilities_tmp

In [5]:

# defines a function to use solver to solve fit_func
def genetic_solver(solver, input_image, original_class, target_class, option, input_file):
    # Have the histories vector
    history = []
    orig_probs = []
    target_probs = []
    
    probabilities_all = []
    
    # Go through each generation
    for j in range(MAX_ITERATION):
        # Generate the solutions
        solutions = solver.ask()
        
        # Calculate the fitness
        fitness_list = np.zeros(solver.popsize)
        
        # Calculate the fitnesses
        for i in range(solver.popsize):
            fitness_list[i] = custom_fitness_function(model, input_to_model, original_class, target_class, rr, cc, solutions[i], option)
            
        solver.tell(fitness_list)
        result = solver.result() # first element is the best solution, second element is the best fitness
        
        orig_prob, target_prob, probabilities = get_predictions_from_temp_array(result, original_class, 
                                                                                target_class, rr, cc)
        
        if (target_prob == np.max(probabilities)):
#             print ("Reached max! Iteration: " + str(j) + " probability:: " + str(target_prob))
#             print ("Top scoring class: ", labels[int(np.argmax(probabilities))])
            
            input_file.write("Reached max! Iteration: " +str(j) + " probability:: " +str(target_prob))
            input_file.write("\n")
            input_file.write("Top scoring class: " + str(labels[int(np.argmax(probabilities))]))
            input_file.write("\n")
            
            import pickle
            pickle_filename = 'pickled_image_parts/target=' + str(target_class)
            pickle_filename += '_original=' + str(original_class) + '.p'
            pickle.dump( result[0], open( pickle_filename, "wb" ) )
            
            return j,history, probabilities_all, orig_probs, target_probs
        
        history.append(result[1])
        orig_probs.append(orig_prob)
        target_probs.append(target_prob)
        probabilities_all.append(probabilities)
        
        if (j+1)%2 == 0:
#             print("fitness at iteration", (j+1), result[1])
#             print ("Target probability: ", target_prob, ":: Original probability: ", orig_prob)
#             print ('Top scorer: ', labels[int(np.argmax(probabilities))], 
#                    ', probability:: ', np.max(probabilities))
            
            input_file.write("fitness at iteration " + str(j+1) + ' ' + str(result[1]))
            input_file.write("\n")
            input_file.write("Target probability: " +str(target_prob) + ":: Original probability: " +str(orig_prob))
            input_file.write("\n")
            input_file.write('Top scorer: '+ str(labels[int(np.argmax(probabilities))]) +
                   ', probability:: ' + str(np.max(probabilities)))
            input_file.write("\n")

#     print("local optimum discovered by solver:\n", result[0])
#     print("fitness score at this local optimum:", result[1])
    return j,history, probabilities_all, orig_probs, target_probs

In [6]:

load_img = utils.LoadImage()
tf_img = utils.TransformImage(model)

import random
for iterations in range(NUMBER_OF_FILES):
    
    xpoint = random.randint(0,299)
    ypoint = random.randint(0,299)
    xpoint2 = random.randint(0,299)
    ypoint2 = random.randint(0,299)
#     xpoint,ypoint,xpoint2,ypoint2 = 13,5,200,210
    print ('Random points: ', xpoint,ypoint,xpoint2,ypoint2)

    # Prep image for inference - load it in and do a bunch of stuff so its ready
    path_img = path + 'imagenet_validation_images/' + random_filenames[iterations]
    input_to_model = prep_image_for_inference(path_img)
    input_to_model = input_to_model.to(device)
    
    rr, cc, val = line_aa(xpoint, ypoint,xpoint2, ypoint2)
    print (len(rr))

    # Get the adversarial line to extract
    adversarial_scratch = input_to_model[:,:,rr,cc]

    # Define the constants we want
    NPARAMS = adversarial_scratch.shape[1] * adversarial_scratch.shape[2]        # make this a 100-dimensinal problem.
    NPOPULATION = 250    # use population size of 200.
    MAX_ITERATION = 1000 # run each solver for 4000 generations.
    import numpy as np

    fitness_option = 0
    original_class = corresponding_index_labels[iterations]

    target_class = random.randint(0,1000)
    
    filename = 'log/imageName_' + random_filenames[iterations]
    filename += '_fitness_' + str(fitness_option)
    filename += '_target=' + str(target_class) 
    filename += '_original=' + str(original_class)
    filename += '_npop=' + str(NPOPULATION)
    filename += '_iters=' + str(MAX_ITERATION)
    filename += 'range_limit'
    filename += '_x0=' + str(xpoint)
    filename += '_y0=' + str(ypoint)
    filename += '_x1=' + str(xpoint2)
    filename += '_y1=' + str(ypoint2)
    log_file= open(filename,"w")

    # defines CMA-ES algorithm solver for each target class
    cmaes = CMAES(NPARAMS,
              popsize=NPOPULATION,
              sigma_init = 0.5
          )

    # Solve a k dimensional problem, and choose 4000 descendants at each iteration
    iterations, scratch, probabilities_all, orig_probs, target_probs = genetic_solver(cmaes, input_to_model, original_class,
                                                                          target_class, fitness_option, log_file)
    print ('Iterations taken: ', iterations)
    log_file.write('Iterations taken: ' + str(iterations))

('Random points: ', 236, 46, 185, 110)
164
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 492 (seed=474756, Wed Jun 12 16:43:52 2019)
('Iterations taken: ', 275)
('Random points: ', 35, 197, 126, 153)
204
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 612 (seed=535609, Wed Jun 12 17:10:05 2019)


/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [194, 195] are not finite but [-inf, -inf]. (class=CMAEvolutionStrategy method=ask iteration=286)
  ')')
/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [20, 28, 84, 100, 111, 209, 212]/[] are nan/None and will be set to the median value -9251.815115745023 (class=CMAEvolutionStrategy method=ask iteration=287)
  ')')
/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [8, 21, 32, 39, 124, 225] are not finite but [-inf, -inf, -inf, -inf, -inf, -inf]. (class=CMAEvolutionStrategy method=ask iteration=287)
  ')')
/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [1, 8, 18, 21, 28, 36, 44, 46, 68, 84, 94, 95, 104, 107, 116, 130, 149, 186, 214, 217, 220, 223, 233, 239]/[] are nan/None

/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [0, 1, 2, 3, 4, 7, 10, 11, 12, 13, 14, 15, 16, 17, 20, 22, 23, 24, 25, 26, 27, 28, 29, 31, 32, 33, 35, 36, 38, 39, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 64, 65, 66, 67, 68, 69, 72, 73, 74, 75, 76, 77, 79, 80, 81, 83, 84, 85, 86, 87, 90, 92, 93, 94, 95, 96, 97, 98, 99, 102, 103, 104, 105, 106, 107, 108, 109, 110, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 127, 128, 130, 131, 132, 134, 135, 136, 137, 139, 140, 142, 143, 144, 145, 146, 148, 150, 151, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 197, 199, 200, 201, 202, 203, 204, 206, 207, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221, 223, 224, 225, 226, 227, 228, 229, 230, 231, 232

/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [0, 1, 2, 3, 4, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 114, 115, 116, 117, 118, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203,

/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199

...

/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: flat fitness (f=-inf, sigma=1.50e+03).
                    For small sigma, this could indicate numerical convergence.
                    Otherwise, please (re)consider how to compute the fitness more elaborately. (iteration=721)
  ')')
/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 

('Iterations taken: ', 999)
('Random points: ', 115, 281, 246, 233)
280
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 840 (seed=523151, Thu Jun 13 08:31:04 2019)
('Iterations taken: ', 489)
('Random points: ', 187, 97, 276, 277)
402
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 1206 (seed=592021, Thu Jun 13 09:17:32 2019)
('Iterations taken: ', 354)
('Random points: ', 257, 125, 225, 103)
79
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 237 (seed=480565, Thu Jun 13 09:54:51 2019)


/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [68, 82, 179]/[] are nan/None and will be set to the median value -13741.390936374704 (class=CMAEvolutionStrategy method=ask iteration=364)
  ')')
/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [104, 188, 227] are not finite but [inf, inf, inf]. (class=CMAEvolutionStrategy method=ask iteration=364)
  ')')
/home/malhar/.local/lib/python2.7/site-packages/cma/utilities/utils.py:333: UserWarning: function values with index [0, 3, 6, 11, 14, 16, 23, 26, 29, 30, 32, 34, 36, 41, 46, 49, 51, 55, 57, 58, 61, 70, 74, 78, 92, 94, 98, 100, 102, 105, 108, 115, 120, 121, 126, 127, 128, 130, 135, 136, 137, 142, 143, 145, 146, 150, 151, 152, 154, 155, 160, 161, 163, 165, 167, 173, 174, 177, 179, 185, 188, 189, 190, 193, 197, 199, 203, 204, 206, 208, 211, 214, 215, 216, 217, 222, 226, 227, 228, 229, 230, 233, 237, 238, 2

('Iterations taken: ', 999)
('Random points: ', 271, 70, 123, 191)
384
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 1152 (seed=530605, Thu Jun 13 11:16:11 2019)
('Iterations taken: ', 233)
('Random points: ', 222, 165, 47, 214)
358
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 1074 (seed=485146, Thu Jun 13 11:41:12 2019)
('Iterations taken: ', 999)
('Random points: ', 184, 171, 89, 299)
320
(125_w,250)-aCMA-ES (mu_w=65.3,w_1=3%) in dimension 960 (seed=561846, Thu Jun 13 13:23:59 2019)


RuntimeError: CUDA error: device-side assert triggered